In [53]:
import os
import glob
import sys 
import json
import geojson
import re
from transliterate import translit, get_available_language_codes

In [54]:
# general fields declaration
RESULT_DIR = "/Users/denyskononenko/Documents/map/results"
MBTILES_DIR = "/Users/denyskononenko/Documents/map/results/mbtiles"
MERGED_FILENAME = "/Users/denyskononenko/Documents/map/results/merged_pol.geojson"
PROCESSED_JSON_FILENAME = "/Users/denyskononenko/Documents/map/results/lun-buildings.geojson"

REGIONS = ["Київ", "Київська область", "Львівська область", "Харківська область", "Дніпропетровська область", "Одеська область"]
REGIONS_TEST = ["Київ"]
HEIGHT_OF_FLOOR = 3
DEFAULT_VALUE_HEIGHT = 5
DEFAULT_MIN_HEIGHT = 0
UNUESED_FILEDS = ["roof:colour", "building", "roof:shape", "opening_hours", "fuel:lpg", "brand"]
#used fields in properties
USED_FILEDS = ["id", "addr:housenumber", "addr:street"]
REPORT_SUMMARY = """
Modification summary 

Init number of features: {}
Final number of features: {}

Buildings without height: {} 
Features with LineString type of geometry: {} 
Deleted Points: {}
Deleted MultiPoints: {}

"""
OUT_BASE = {
   "type": "FeatureCollection",
   "features": []
    }

filenames = []



In [56]:
# functions declaration
def update_progress(progress, maxl):
    """ Update custom progress bar."""
    bar_length = 20
    interval = maxl
    block = int(round(bar_length*progress))
    text = "\rProgress: [{0}] {1}% ".format( "#"*block + "-"*(bar_length-block), round(100*(progress + 1)/interval, 2))
    sys.stdout.write(text)
    sys.stdout.flush()


def start_pipeline_to_geojson():
    """Steps for generation of total geojson"""
    # get xml files from osm
    print("XML obtaining")
    for index, region in enumerate(REGIONS):
            # progeress bar
            update_progress(index, len(REGIONS))
            filename = region.replace(" ", "_")
            filenames.append(filename)
            os.system('python3 getosm.py "{0}" > {2}/{1}.xml'.format(region, filename, RESULT_DIR))
            
            
    # make geojson files from xml
    os.chdir(RESULT_DIR)
    print("\nGenerating of geojson:")
    for index, filename in enumerate(filenames):
        update_progress(index, len(filenames))
        os.system('node --max_old_space_size=4000 `which osmtogeojson` {0}.xml > {0}.geojson'.format(filename))
    
    # open base file
    with open('{}.geojson'.format(filenames[0])) as geojson1:
        poly_base_geojson = json.load(geojson1)

    # merdge features of the base file with other
    print("\n Merging")
    for index, file in enumerate(filenames[1:]):
        with open('{}.geojson'.format(file)) as geojson_temp:
            poly_temp_geojson = json.load(geojson_temp)
        # add to features of the next 
        poly_base_geojson['features'] += poly_temp_geojson['features']
        update_progress(index, len(filenames[1:]))

    with open(MERGED_FILENAME, 'w') as outfile:
            json.dump(poly_base_geojson, outfile, indent=3)
    
    return poly_base_geojson
    
def process_geojson(poly_base_geojson):
    """
    Add field height and if it is absent in Property of Feature.
    Save processed geojson in separate file. 
    """
    count_build_without_height = 0
    count_bug_linestring = 0
    count_deleted_points = 0
    count_deleted_multi_points = 0
    count_deleted_unused_fields = 0
    init_features_number = len(poly_base_geojson["features"])
    
    out_json = OUT_BASE.copy()
    try:
        for item in poly_base_geojson["features"]:
            temp_item = {}
            temp_item["type"] = item["type"]
            temp_item["id"] = item["id"]
            # init properties
            temp_item["properties"] = {}
            # init geometry
            temp_item["geometry"] = {}
            
            properties = item["properties"]
            geom_type = item["geometry"]["type"]
            if geom_type == "Point":
                count_deleted_points += 1
            else:
                # build properties
                #make dafault value of height if absent
                if "height" in properties:
                    temp_item["properties"]["height"] = float(re.sub(r"[;,]", ".", re.sub(r"[a-z'`]", "", item["properties"]["height"])))
                elif "height" not in properties and "building:levels" not in properties:
                    temp_item["properties"]["height"] = DEFAULT_VALUE_HEIGHT
                    count_build_without_height += 1
                elif "height" not in properties and len(re.sub(r"[^0-9^.]", "", item["properties"]["building:levels"])) > 0:
                    #check presence of several values in building levels like 3;2;2 or 16-22
                    # if yes get first value
                    print(item["id"])
                    print(item["properties"]["building:levels"])
                    temp_height = re.findall(r"[0-9]+", item["properties"]["building:levels"])[0]
                    print(temp_height)
                    # remove all symbols except number from the building:levels field and calculate height field
                    temp_item["properties"]["height"] = HEIGHT_OF_FLOOR * float(re.sub(r"[;,]", ".", re.sub(r"[^0-9^.]", "", temp_height)))
                else:
                    temp_item["properties"]["height"] = DEFAULT_VALUE_HEIGHT
                    
                # add another fields if applicable
                for field in USED_FILEDS:
                    if field in item["properties"]:
                        temp_item["properties"][str(field)] = item["properties"][str(field)]
                        #print(temp_item)
                        count_deleted_unused_fields += 1
                        
                # add `min_height` field
                if "min_heihgt" in item["properties"]:
                    #add min height
                    min_height = float(re.sub(r"[a-z]", "", item["properties"]["min_height"]))
                    if min_height < 0:
                        min_height = 0
                    temp_item["properties"]["min_height"] = min_height
                else:
                    #add default value
                    temp_item["properties"]["min_height"] = DEFAULT_MIN_HEIGHT

                # build geometry
                # correct LineString geometry type to Polygon
                geom_coordinates = item["geometry"]["coordinates"]
                if geom_type == "LineString":
                    temp_item["geometry"]["coordinates"] = [geom_coordinates]
                    temp_item["geometry"]["type"] = "Polygon"
                    count_bug_linestring += 1
                else:
                    temp_item["geometry"]["coordinates"] = geom_coordinates
                    temp_item["geometry"]["type"] = geom_type
                    
                #add corrected feature to result
                out_json["features"] += [temp_item]
                        
    except TypeError as error:
        print(error)
        print(type(item))
        
    final_features_number = len(out_json["features"])
    #save corrected json in the file
    with open(PROCESSED_JSON_FILENAME, 'w') as outfile:
        json.dump(out_json, outfile, indent=3)
    # print report 
    print(REPORT_SUMMARY.format(init_features_number, final_features_number, count_build_without_height, count_bug_linestring, count_deleted_points, count_deleted_multi_points))
    
def test_height_number():
    id_without_height = []
    
    with open(PROCESSED_JSON_FILENAME) as geojson_temp:
        proc = json.load(geojson_temp)

    for feature in proc["features"]:
        if "height" not in feature["properties"]:
            id_without_height.append(feature["id"])
    
    print("\n Buildings without height id: {} \n Total num {} \n Without height num {}".format(id_without_height, len(proc["features"]), len(id_without_height)))

def test_height_value():
    high_build = []
    with open(PROCESSED_JSON_FILENAME) as geojson_temp:
        proc = json.load(geojson_temp)
    
    for feature in proc["features"]:
        if feature["properties"]["height"] >= 168:
            high_build.append(feature["id"])
    print("\nID of buildings wiht large height:\n {}".format(high_build))
    

In [47]:
#base = start_pipeline_to_geojson()
print("\n\nProcessing of geojson")
with open(MERGED_FILENAME) as geojson_temp:
            base = json.load(geojson_temp)
process_geojson(base)



Processing of geojson
relation/1015779
2
2
relation/1210126
2
2
relation/5509188
2
2
relation/1015778
2
2
relation/1015777
2
2
relation/1741655
3
3
relation/1745239
2
2
relation/5259419
3
3
relation/5249544
2
2
relation/5163854
14
14
relation/4064207
6
6
relation/4041520
5
5
relation/4042843
1
1
relation/4051053
1
1
relation/4051054
2
2
relation/4051055
4
4
relation/4051144
3
3
relation/4051158
3
3
relation/4042795
1
1
relation/4042797
4
4
relation/4042841
2
2
relation/4049547
1
1
relation/3483811
3
3
relation/3483809
2
2
relation/4192125
3
3
relation/4192124
3
3
relation/4192126
3
3
relation/2837432
3
3
relation/1727455
2
2
relation/7318713
2
2
relation/2175397
2
2
relation/9500435
3
3
relation/2108235
11
11
relation/3784124
4
4
relation/1897654
2
2
relation/2012826
1
1
relation/2012824
2
2
relation/2012827
3
3
relation/2133172
3
3
relation/6588414
2
2
relation/6588415
3
3
relation/1447306
2
2
relation/1447398
2
2
relation/1447399
2
2
relation/271481
4
4
relation/1845808
3
3
relatio

way/174550387
1
1
way/428087556
2
2
way/613274848
1
1
way/613274849
1
1
way/100400805
5
5
way/100400809
9
9
way/100400820
5
5
way/100400893
5
5
way/100400905
9
9
way/100400916
5
5
way/100506598
2
2
way/100506655
9
9
way/100506673
5
5
way/100506719
9
9
way/100506720
9
9
way/100506728
9
9
way/100506792
5
5
way/100506824
2
2
way/100506830
9
9
way/100506833
9
9
way/100506839
5
5
way/100506863
16
16
way/100506899
2
2
way/100507013
9
9
way/100507023
2
2
way/100507025
5
5
way/100507030
5
5
way/105209325
1
1
way/105209336
2
2
way/105209341
2
2
way/348412089
1
1
way/463530699
21
21
way/43337716
9
9
way/43337717
16
16
way/100400776
7
7
way/100400878
18
18
way/100506592
16
16
way/100506680
9
9
way/100506683
9
9
way/100506810
5
5
way/100506848
9
9
way/100506925
16
16
way/100506935
9
9
way/100506947
9
9
way/100506958
2
2
way/100506979
1
1
way/100506988
2
2
way/100507005
9
9
way/100507008
9
9
way/105209335
16
16
way/105209357
16
16
way/105209359
4
4
way/105645301
16
16
way/105645304
16
16
way/105645

2
way/118581778
2
2
way/226825848
1
1
way/226825863
2
2
way/240105116
3
3
way/240105117
3
3
way/240105118
3
3
way/343042780
1
1
way/343042798
5
5
way/349559879
1
1
way/150359476
2
2
way/150359481
2
2
way/150359494
1
1
way/150359503
2
2
way/236814410
1
1
way/236814458
1
1
way/236814715
1
1
way/304925408
1
1
way/317990819
7
7
way/343042772
16
16
way/343042774
16
16
way/343042783
1
1
way/343042787
3
3
way/343042789
2
2
way/343042794
2
2
way/39693163
16
16
way/150642873
6
6
way/352153628
2
2
way/352153633
1
1
way/352153659
1
1
way/352153701
1
1
way/100506941
3
3
way/104221586
3
3
way/150641212
2
2
way/150642880
1
1
way/150642885
1
1
way/150642914
1
1
way/152021688
2
2
way/317634879
1
1
way/317634880
2
2
way/317636740
7
7
way/352153638
1
1
way/352153643
1
1
way/352153652
1
1
way/352153666
1
1
way/352153667
1
1
way/352153686
1
1
way/352153704
1
1
way/352153705
1
1
way/352153711
1
1
way/352153712
1
1
way/353525427
2
2
way/421145981
5
5
way/613243283
1
1
way/73368155
9
9
way/73368157
1
1
way/7

5
5
way/100738934
4
4
way/100738993
4
4
way/100739146
4
4
way/100739297
9
9
way/100739339
3
3
way/105072584
16
16
way/114122267
3
3
way/114122268
5
5
way/127710494
17
17
way/129317945
2
2
way/129819814
3
3
way/130046645
2
2
way/131395733
5
5
way/155455177
5
5
way/160901443
1
1
way/160903044
1
1
way/162734931
17
17
way/320800608
2
2
way/329118452
1
1
way/366722387
1
1
way/380011023
1
1
way/476679994
1
1
way/476949283
1
1
way/31726405
12
12
way/54848294
2
2
way/86814891
25
25
way/86815055
16
16
way/86815169
16
16
way/86815219
18
18
way/100506708
1
1
way/100506916
3
3
way/100506960
5
5
way/105072600
2
2
way/131389372
6
6
way/131389373
2
2
way/150512831
5
5
way/150515209
2
2
way/150516592
3
3
way/155455171
5
5
way/160770302
1
1
way/160770304
2
2
way/160901390
2
2
way/160901425
9
9
way/160901434
2
2
way/160901456
2
2
way/185026137
9
9
way/325900055
2
2
way/379798049
1
1
way/451542133
1
1
way/451545826
2
2
way/451545834
1
1
way/451545837
2
2
way/451545839
1
1
way/451545862
1
1
way/37385809
5

16
way/100224605
5
5
way/100224689
2
2
way/100224703
9
9
way/100224711
5
5
way/100224714
5
5
way/100224739
5
5
way/100224747
5
5
way/100224762
5
5
way/100224770
1
1
way/100224796
5
5
way/100224847
5
5
way/100224871
16
16
way/100224881
3
3
way/105815925
1
1
way/105815970
5
5
way/105815985
1
1
way/105815992
1
1
way/105816057
4
4
way/105816100
5
5
way/105816121
2
2
way/384758893
1
1
way/431589272
1
1
way/688577123
1
1
way/688840223
9
9
way/691401517
1
1
way/50554587
5
5
way/100224543
5
5
way/100224559
5
5
way/100224569
5
5
way/100224583
5
5
way/100224587
5
5
way/100224606
9
9
way/100224612
5
5
way/100224626
5
5
way/100224630
3
3
way/100224633
2
2
way/100224641
9
9
way/100224668
9
9
way/100224690
5
5
way/100224710
5
5
way/100224719
5
5
way/100224730
9
9
way/100224745
5
5
way/100224754
5
5
way/100224763
5
5
way/100224768
5
5
way/100224788
5
5
way/100224790
9
9
way/100224795
5
5
way/100224797
2
2
way/100224804
5
5
way/100224820
5
5
way/100224829
5
5
way/100224849
5
5
way/100224854
5
5
way/10

...

5
5
way/160122220
7
7
way/160122228
3
3
way/160122236
3
3
way/160122246
3
3
way/160122261
4
4
way/160122268
8
8
way/160122276
4
4
way/160122278
9
9
way/160122281
5
5
way/160122288
3
3
way/160122298
4
4
way/160122307
1
1
way/160122361
4
4
way/160136909
2
2
way/160139862
3
3
way/160139865
2
2
way/160454304
4
4
way/160454384
2
2
way/160454395
3
3
way/160454434
3
3
way/160454439
4
4
way/160458228
3
3
way/160458233
5
5
way/160458240
3
3
way/160458252
4
4
way/160458254
3
3
way/160458264
3
3
way/160458278
3
3
way/160458294
2
2
way/160458295
4
4
way/160458299
3
3
way/160458300
3
3
way/160458304
3
3
way/160458311
4
4
way/160458312
5
5
way/160458328
2
2
way/160458330
5
5
way/160458334
3
3
way/160458342
4
4
way/160465487
3
3
way/160465502
3
3
way/160465504
2
2
way/160465528
4
4
way/160465537
3
3
way/160465620
5
5
way/160465624
2
2
way/160465627
2
2
way/160465632
3
3
way/160465654
3
3
way/163403889
3
3
way/163403893
3
3
way/163403923
4
4
way/185055411
3
3
way/187922264
2
2
way/221876987
3
3
way/22

2
way/450634456
4
4
way/450634457
2
2
way/450634458
3
3
way/450634463
1
1
way/450634467
1
1
way/450634469
1
1
way/450634470
5
5
way/450634471
2
2
way/450634475
2
2
way/450634476
2
2
way/450634479
1
1
way/450634482
1
1
way/450634483
1
1
way/451804386
3
3
way/467747431
2
2
way/467747432
1
1
way/467747453
1
1
way/467747459
2
2
way/468017191
4
4
way/468321639
3
3
way/468321643
4
4
way/468321644
4
4
way/468321656
2
2
way/597047146
2
2
way/597047147
2
2
way/597047148
3
3
way/161030592
5
5
way/161030599
10
10
way/161030643
11
11
way/161030650
9
9
way/161030652
16
16
way/161030684
2
2
way/161030687
18
18
way/161030696
4
4
way/161030719
2
2
way/161030722
2
2
way/323235996
2
2
way/323236003
2
2
way/323236008
1
1
way/388396033
1
1
way/388589541
1
1
way/388589544
3
3
way/396704099
3
3
way/467979627
1
1
way/561084025
1
1
way/38046967
2
2
way/160231635
3
3
way/160231730
4
4
way/160351750
2
2
way/161030605
3
3
way/161030634
3
3
way/161030662
5
5
way/161030683
3
3
way/161034452
5
5
way/208385137
3
3
w

way/354584040
1
1
way/354584043
1
1
way/354584045
1
1
way/375072253
2
2
way/388119276
2
2
way/388119278
1
1
way/440470665
6
6
way/440470668
7
7
way/440470673
8
8
way/492430586
1
1
way/504618138
1
1
way/591678572
8
8
way/591678573
8
8
way/192511093
10
10
way/192511094
10
10
way/193016446
10
10
way/193016450
10
10
way/193111604
10
10
way/193111605
10
10
way/193111606
10
10
way/193111608
9
9
way/193120336
10
10
way/193120337
11
11
way/193120338
9
9
way/193120339
10
10
way/196283264
19
19
way/196283269
19
19
way/196283272
19
19
way/200885092
2
2
way/200885095
2
2
way/200885097
2
2
way/200885100
2
2
way/328867935
16
16
way/328951211
1
1
way/329004361
6
6
way/329004363
6
6
way/329004364
2
2
way/335033387
2
2
way/335033388
2
2
way/335033389
2
2
way/335033390
2
2
way/335033392
2
2
way/335033393
2
2
way/335033394
2
2
way/335033395
2
2
way/335033396
2
2
way/335033398
2
2
way/335033399
2
2
way/335033400
2
2
way/335033401
2
2
way/335033402
2
2
way/335033403
2
2
way/335033404
2
2
way/335033406
2
2


2
2
way/196766934
1
1
way/196873680
3
3
way/196961894
1
1
way/196961897
1
1
way/329014049
3
3
way/387004483
1
1
way/387146948
1
1
way/387826950
1
1
way/389394566
1
1
way/396063886
1
1
way/435070868
1
1
way/446430262
1
1
way/446430264
1
1
way/446430282
1
1
way/492430601
1
1
way/492430603
1
1
way/520599534
9
9
way/521087265
1
1
way/135733437
9
9
way/183365310
5
5
way/183365312
6
6
way/183365318
2
2
way/183365328
4
4
way/184160272
5
5
way/184160276
2
2
way/184160284
2
2
way/184160286
2
2
way/184160295
1
1
way/190631409
6
6
way/191433080
16
16
way/191433090
12
12
way/191433091
14
14
way/191433092
16
16
way/191433099
9
9
way/191433104
9
9
way/191433112
9
9
way/262336055
2
2
way/321575138
1
1
way/351959736
3
3
way/375072249
3
3
way/387004510
1
1
way/387004516
10
10
way/387004517
1
1
way/387004520
2
2
way/387148501
10
10
way/388119307
1
1
way/388577217
1
1
way/446430292
8
8
way/504458301
1
1
way/504458303
1
1
way/504618080
1
1
way/515011049
1
1
way/515011050
1
1
way/515090969
1
1
way/51527165

16
way/276452500
9
9
way/276452502
16
16
way/276455807
9
9
way/276455813
9
9
way/276455818
16
16
way/222034786
9
9
way/276293790
9
9
way/276455817
16
16
way/227761631
9
9
way/231492914
9
9
way/276347940
9
9
way/276452470
9
9
way/276452473
9
9
way/276452475
9
9
way/276452479
9
9
way/276452482
5
5
way/276455810
2
2
way/394752770
9
9
way/464059430
1
1
way/459356411
2
2
way/459356412
2
2
way/459356413
1
1
way/461128294
1
1
way/492768491
7
7
way/394752771
9
9
way/222034787
9
9
way/276293791
9
9
way/276452478
9
9
way/451237708
1
1
way/451237710
1
1
way/445145868
2
2
way/445237046
1
1
way/451237665
1
1
way/451237667
1
1
way/451237672
1
1
way/451237674
1
1
way/451237676
1
1
way/451237677
1
1
way/451237679
1
1
way/451237681
1
1
way/451237683
1
1
way/451237684
1
1
way/451237686
1
1
way/451237688
1
1
way/451237690
1
1
way/451237691
1
1
way/451237693
1
1
way/451237695
1
1
way/445790360
3
3
way/452308430
2
2
way/451956437
1
1
way/451956438
1
1
way/451956439
1
1
way/451956440
1
1
way/451956441
1
1
w

In [ ]:
# make mbtile
os.system('tippecanoe -o {}.mbtiles {}.geojson'.format("lnbuildings", PROCESSED_JSON_FILENAME))

In [57]:
test_height_number()
test_height_value()


 Buildings without height id: [] 
 Total num 1345595 
 Without height num 0

ID of buildings wiht large height:
 ['way/412916330', 'way/413879142', 'way/409948785', 'way/412915563']


In [ ]:
files = []
os.chdir(RESULT_DIR)
for file in glob.glob("*.geojson"):
    files.append(file)
    print(file)

In [ ]:
# open base file
print(files[0])
with open(files[0]) as geojson1:
    poly_base_geojson = json.load(geojson1)

# merdge features of the base file with other
print("\n Merging")
for index, file in enumerate(files[1:]):
    with open(file) as geojson_temp:
        print(file)
        poly_temp_geojson = json.load(geojson_temp)
    # add to features of the next 
    poly_base_geojson['features'] += poly_temp_geojson['features']
    update_progress(index, len(files[1:]))
    
with open(MERGED_FILENAME, 'w') as outfile:
    json.dump(poly_base_geojson, outfile, indent=3)

In [52]:
stri = "3;2;2"
stri2 = "+16.1`+-22`"
stri3 = "10,9"
stri4 = "-1"

temp_str = stri3.split("-")[0]
temp_str = temp_str.split(";")[0]
print(re.findall(r"[0-9]+", stri2)[0])

16
